In [1]:
from diskcache_class import db
from lda_mallet import *
from pre_processing import *
from os import walk
from tqdm import tqdm

[nltk_data] Downloading package stopwords to /Users/das-
[nltk_data]     lab/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /Users/das-lab/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /Users/das-lab/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/das-lab/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


In [2]:
#we are going to run this on 4 different dataset 1. EDML 2. AP 3. Newsgroup 4.Covid-Tweet


############################## reading data for ED corpus
datafolder = './data/ed_recovery_formatted/Excel'
#datafolder = 'ed_recovery_topicmodel'
df = pd.DataFrame(columns=['url','type','photo','date','tags','notes','text','photo_url','reblogged','blog_name'])

for dirpath,dirnames,filenames in walk(datafolder):
  for filename in filenames:
    if filename.endswith('.xlsx'):
      t = pd.read_excel(datafolder+'/'+filename,names=['url','type','photo','date','tags','notes','text','photo_url','reblogged'])
      blog_name = t.iloc[0,0].split(':')[1]
      t['blog_name'] = blog_name
      df = df.append(t.iloc[3:,:],ignore_index=True)
      print('blog:{0}   with posts:{1}    and reblogs:{2}  '.format(filename,len(t),len(t[t.reblogged=='yes'])))


print('number of blogs: {0} - number of posts: {1}'.format(len(set(df.blog_name)),len(df)))
print('out of {0} documents, {1} are reblogged.'.format(len(df),len(df[df.reblogged == 'yes'])))

#finding reblogged texts
texts = sorted(df.text) #sort them to keep smallest post (perhaps original one) at first
re_texts = []

while len(texts):
  t = [texts.pop(0)]#pop first text and find it!
  if t[0] == ' ' or len(t[0].split())<3: 
    continue #almost nothing to look
  i = 0
  while i<len(texts):
    if t[0] in texts[i]:
      t.append(texts.pop(i))
    else:
      i += 1
  if len(t) > 1:
    re_texts.append(t)


print('number of unique reblogged texts: {0}'.format(len(re_texts)))
print('number of unique string in all texts: {0}'.format(len(set(df.text))))

extra_stopwords = ['isnt','want','cant','wanna','im','could','ive','would','dont','get','also','us','thats','got','ur','wanted',
                   'may', 'the', 'just', 'can', 'think', 'damn', 'still', 'guys', 'literally', 'hopefully', 'much', 'even', 'rly', 'guess', 'anon']#anything with a length of one
                   

'''pre-processing'''
# original_doc_set = list(df.text[df.photo=='no'])
sel_df = df[df.photo=='no'] #extracting only-text posts
doc_list = list(sel_df.text)


# ##############reading AP corpus
# text_df = ap_corpus('./data/ap.txt')
# doc_list = list(text_df.text_cleaned)

##############reading Newsgroup corpus
# text_df = newsgroup('./data/20newsgroup_preprocessed.csv')
# doc_list = list(text_df.text_cleaned)

##############Covid Tweet corpus
# doc_list=[]
# with open('./data/covid_tweets','r',encoding='utf-8') as txtfile:
#     doc_list = txtfile.readlines()


#loading ref corpus for coherene score for lda_mallet
wiki_docs = loading_wiki_docs('./data/wiki_sampled_10p.txt')
#doing pre-processing on wiki-pedia documents
pre_processed_wiki, _ = preprocess_data(wiki_docs)
wiki_vocab_dict, _ = prepare_corpus(pre_processed_wiki)
del wiki_docs

blog:mote-of-dust_formatted.xlsx   with posts:271    and reblogs:238  
blog:fuck-eatingdisorders_formatted.xlsx   with posts:37    and reblogs:4  
blog:hellsite-residential_formatted.xlsx   with posts:247    and reblogs:191  
blog:lets-get-better_formatted.xlsx   with posts:509    and reblogs:453  
blog:bagelbells_formatted.xlsx   with posts:1101    and reblogs:1046  
blog:imtrying-butimpissed_formatted.xlsx   with posts:838    and reblogs:483  
blog:faithhopeloveandtherapy_formatted.xlsx   with posts:2994    and reblogs:1510  
blog:finallyrecoveringforgood_formatted.xlsx   with posts:137    and reblogs:49  
blog:intentandotrascender_formatted.xlsx   with posts:21    and reblogs:0  
blog:fearless-foodie_formatted.xlsx   with posts:3956    and reblogs:3670  
blog:ariessuntaurusrising_formatted.xlsx   with posts:504    and reblogs:206  
blog:rec-hovery_formatted.xlsx   with posts:22    and reblogs:7  
blog:shameofateen_formatted.xlsx   with posts:54    and reblogs:2  
blog:brittle-bunny_

In [3]:
#removing terms that are not in Wikipedia ref-corpus
pre_processed_docs,filtered_docs = preprocess_data(doc_list,extra_stopwords={})
#generate vocabulary and texts
vocab_dict, doc_term_matrix = prepare_corpus(pre_processed_docs)

#finding stopwords that are not in Wikipedia and removing those
extra_stopwords = set(vocab_dict.token2id.keys()).difference(set(wiki_vocab_dict.token2id.keys()))
pre_processed_docs,filtered_docs = preprocess_data(doc_list,extra_stopwords=extra_stopwords)
vocab_dict, doc_term_matrix = prepare_corpus(pre_processed_docs)

In [ ]:
#running many many LDA and storing their pair of terms
import numpy as np

start = 6; limit=13; step = 1
runs = 3
iterations = 5000
term_pairs = set()

for num_topics in tqdm(range(start, limit+1, step)):
    model_t = []
    purity_t = []
    coherence_t = []
    contrast_t = []
    for iter in np.random.permutation(iterations).tolist()[0:10]:
        #model=LdaModel(corpus=corpus, id2word=dictionary, num_topics=num_topics)
        model = LdaMallet(mallet_path, corpus=doc_term_matrix, num_topics=num_topics, id2word=vocab_dict,optimize_interval = 25,workers=1, iterations=iter)

        #storing top_terms
        for tn in range(num_topics): 
            tt = model.show_topic(tn,topn=20)

            #saving top_terms and their counts
            top_terms = [i[0] for i in tt]

            #making pair terms
            for i in range(len(top_terms)):
                for j in range(i+1,len(top_terms)):
                    term_pairs.add((top_terms[i],top_terms[j]))
    

  0%|                                                     | 0/8 [00:00<?, ?it/s]Mallet LDA: 6 topics, 3 topic bits, 111 topic mask
Data loaded.
max tokens: 537
total tokens: 170848
<10> LL/token: -8.44246
<20> LL/token: -8.00181
<30> LL/token: -7.80491
<40> LL/token: -7.72189

0	8.33333	feel time back weight made long feeling days normal run question past feels times hard lot make running answer start 
1	8.33333	im dont feel love calories answer shit life ur bc hope lol gonna stop fuck guess control question live ive 
2	8.33333	people question answer things find life person lot makes hard world friend kind make thing feel wrong difficult child safe 
3	8.33333	therapy week session things bit talk therapist felt end back time thought talking part started thinking told parents asked head 
4	8.33333	day today home time baby good fucking family morning nice great bad friends pretty night house weeks tomorrow hours stay 
5	8.33333	eating eat food body recovery ed disorder good make healthy w

<460> LL/token: -7.68339
<470> LL/token: -7.68472
[beta: 0.08458] 
<480> LL/token: -7.67863
<490> LL/token: -7.68193

0	4.59206	feel time make life back bad hard work long feeling things brain thing days body stop start feels point mind 
1	2.08341	im dont shit fucking ur bc lol gonna fuck ive literally hate wanna money ass guess people sick ppl ill 
2	4.03539	question answer people hope love care lot school person post friends things mental kind health tumblr find trauma uk anon 
3	3.61992	therapy session week talk bit things therapist felt thought end talking good thinking told parents time back asked stuff mum 
4	3.49858	day today good home time baby morning made run night family nice days tomorrow bed back inpatient house hours room 
5	2.62041	eating eat food weight recovery disorder body calories ed binge good healthy cake ate lunch lose meals meal breakfast normal 

[beta: 0.0855] 
<500> LL/token: -7.67521
<510> LL/token: -7.6829
<520> LL/token: -7.67915
[beta: 0.08729] 
<530> LL/

<910> LL/token: -7.74213
<920> LL/token: -7.73958
[beta: 0.12659] 
<930> LL/token: -7.74373
<940> LL/token: -7.73788

0	0.80949	recovery feel people eating life ed disorder things body time bad hard make back lot love person thing brain world 
1	0.37915	im dont feel ur shit fucking lol bc gonna life ive fuck time people make literally ass wanna hate love 
2	0.55883	question answer people school care family uk time hope parents anon year baby years tumblr children love friends foster hospital 
3	0.59301	therapy session feel things therapist week talk time bit back felt talking thought end good thinking asked feeling told mum 
4	0.61443	day today time good home days morning back run night baby bed hours tomorrow house inpatient sleep friends week bad 
5	0.35373	eat food eating weight calories body binge good cake healthy meals ate lunch day breakfast meal make feel foods diet 

[beta: 0.12986] 
<950> LL/token: -7.74089
<960> LL/token: -7.73515
<970> LL/token: -7.7395
[beta: 0.13042] 
<98

<1360> LL/token: -7.71054
<1370> LL/token: -7.70417
[beta: 0.16131] 
<1380> LL/token: -7.70717
<1390> LL/token: -7.70593

0	0.25926	recovery people eating life feel ed disorder things body love make hard time world trauma person hope bad mental lot 
1	0.198	im dont feel ur shit fucking people lol life time bc make gonna fuck ive good ass back literally wanna 
2	0.19657	answer question people school uk time family hope baby care anon year home back parents week foster children hospital friends 
3	0.23751	therapy session feel time things therapist week talk bit felt talking back thought good end asked question feeling thinking thing 
4	0.23495	day today time good back morning home days night run baby feel bed bad tomorrow inpatient hours friends room sleep 
5	0.17782	eat eating food weight calories body binge good feel day time cake healthy meals lunch ate make lose foods breakfast 

[beta: 0.1631] 
<1400> LL/token: -7.70732
<1410> LL/token: -7.70435
<1420> LL/token: -7.70418
[beta: 0.16

<1810> LL/token: -7.68752
<1820> LL/token: -7.6847
[beta: 0.16885] 
<1830> LL/token: -7.68892
<1840> LL/token: -7.69086

0	0.22329	recovery people eating life disorder things ed feel love body hope back hard lot person question make time world trauma 
1	0.17585	im dont feel ur time fucking shit people lol life make bc gonna ive fuck literally ass good wanna answer 
2	0.14656	question answer people school time uk baby home family care back week year foster years parents hospital long children anon 
3	0.1992	therapy feel session things time therapist talk week bit felt talking back good end thought question asked answer make hard 
4	0.18877	day today time good home morning feel days back run baby night bed friends bad tomorrow made inpatient running sleep 
5	0.15339	eat eating food weight calories body binge feel good day time cake healthy make meals ate meal ed lose today 

[beta: 0.17009] 
<1850> LL/token: -7.68746
<1860> LL/token: -7.68613
<1870> LL/token: -7.69044
[beta: 0.16878] 
<1

...

<2660> LL/token: -7.73839
<2670> LL/token: -7.73837
[beta: 0.09194] 
<2680> LL/token: -7.73754
<2690> LL/token: -7.7368

0	0.1643	answer question hope recovery ed tumblr people anon post blog posts kind pro hey love feel good follow find message 
1	0.13201	people love feel things friends make person friend deserve care life makes thing mental world health good bad hard find 
2	0.0842	day inpatient hospital bad good answer question friends staff today pretty time lot unit room feel made great nice treatment 
3	0.15758	day today time baby run home morning running back night house days bed hours sleep good tomorrow evening week walk 
4	0.08449	question answer school uk baby people year home family foster babies care children vaccine time parents week kids back live 
5	0.19608	therapy session things week talk feel time therapist bit felt talking back thought end asked good feels thinking talked thing 
6	0.14911	im dont ur shit fucking lol bc ive time feel gonna fuck life make ass literally

<120> LL/token: -7.6274
<130> LL/token: -7.61514
<140> LL/token: -7.61979

0	4.16667	eating food eat body weight recovery ed disorder binge healthy stop control lose meals meal foods hungry fat number problem 
1	4.16667	im dont fucking ur life bc lol gonna fuck ive literally care hate money wanna ass make people reason give 
2	4.16667	today days day good great full hours home ate cake eat lunch house yesterday made water breakfast morning dinner energy 
3	4.16667	feel calories shit make thing making start feels made makes person guess small needed stop free fact diet matter honestly 
4	4.16667	day bad friends good time nice friend pretty night lot room inpatient hard mental anxiety anxious worth morning sleep walk 
5	4.16667	back baby talking year parents weeks time family mum relationship couple child care made uk big home babies children faith 
6	4.16667	feel things people lot find brain stuff good make point remember change working makes experience hear means learn starting thing 
7

<360> LL/token: -7.72609
<370> LL/token: -7.73895
[beta: 0.0399] 
<380> LL/token: -7.71705
<390> LL/token: -7.73065

0	2.09019	eating weight body recovery food ed disorder eat healthy lose control number stop disorders recover gain normal pro size skinny 
1	1.73482	im dont shit fucking ur lol gonna bc fuck ive literally money wanna ass hate ppl ill guess gotta reason 
2	1.40718	eat food good ate cake lunch meal breakfast meals today hungry dinner day full coffee make eaten evening eating chocolate 
3	1.29338	calories binge small water diet girl drink low free sugar put culture cup remember stop stomach fun sucks stupid stress 
4	2.15426	day today bad good friends morning friend made night days nice great pretty inpatient lot anxiety room sleep hospital tomorrow 
5	1.8463	school baby year family home weeks parents uk babies children care back lovely job social lockdown group week ago girls 
6	2.69175	feel people things lot good find make makes brain thing hard real understand hear post 

<160> LL/token: -7.60725
<170> LL/token: -7.60126
<180> LL/token: -7.59977
<190> LL/token: -7.60281

0	4.16667	thing disorder make brain eating life feels time start point taking sense cake process kind change part easy times weird 
1	4.16667	made years school year time parents past mum friend ago wrong big child left anxiety coming told adult problem side 
2	4.16667	eat eating food recovery ed full bad days lunch meals meal breakfast hungry dinner stop foods recover posts normal enjoy 
3	4.16667	im dont shit fucking ur bc lol gonna fuck ive literally hate life wanna money ass deserve make ppl give 
4	4.16667	day today days hope morning run nice tomorrow happy running hours evening call yesterday weeks rest sitting room lovely phone 
5	4.16667	question answer friends bad long pretty lot inpatient great tumblr uk anxious treatment good hospital safe allowed positive super staff 
6	4.16667	time hard feel therapist back work things feeling find relationship make face person important work

<210> LL/token: -7.58074
<220> LL/token: -7.58005
[beta: 0.02379] 
<230> LL/token: -7.62615


In [56]:
#converting set to list
term_pairs_ls = [[i[0],i[1]] for i in list(term_pairs)]

In [58]:
#computing Coherence for all term pairs
cscore = CoherenceModel(topics=term_pairs,dictionary=wiki_vocab_dict,texts=pre_processed_wiki,coherence='c_npmi',processes=3,topn=2).get_coherence_per_topic()


In [61]:
#Loading the DB
npmi_db = db('./db/wiki_5p_old')


Load NPMI coherence DB. 
Number of keys : 213440


In [60]:
#writing into the DB
for i in tqdm(range(len(term_pairs_ls))):
    #if the key does not exist, insert it
    try:
        npmi_db.db[(term_pairs_ls[i][0],term_pairs_ls[i][1])]
    except:
        npmi_db.db[(term_pairs_ls[i][0],term_pairs_ls[i][1])] = cscore[i]
    #do the other combination
    try:
        npmi_db.db[(term_pairs_ls[i][1],term_pairs_ls[i][0])]
    except:
        npmi_db.db[(term_pairs_ls[i][1],term_pairs_ls[i][0])] = cscore[i]

100%|████████████████████████████████████| 34642/34642 [00:39<00:00, 878.90it/s]


# Generating new NPMIs for a new corpus

In [3]:
old_db = db('./db/wiki_5p_old')
new_db = db('./db/wiki_10p')

Load NPMI coherence DB. 
Number of keys : 364450
Load NPMI coherence DB. 
Number of keys : 181604


In [4]:
#loading ref corpus for coherene score for lda_mallet
abs_path = 'G:\wiki_corpus_gensim\wiki20p0'
wiki_docs = loading_wiki_docs(abs_path)
#doing pre-processing on wiki-pedia documents
pre_processed_wiki, _ = preprocess_data(wiki_docs)
wiki_vocab_dict, _ = prepare_corpus(pre_processed_wiki)
del wiki_docs

MemoryError: 

In [36]:
term_pairs = set()
max_ins = 60000
count = 0

for k in old_db.db.iterkeys():
    #check if it is already in the list but in reverse order + if it is in the vocab
    if (k[1],k[0]) not in term_pairs and k[0] in wiki_vocab_dict.token2id.keys() and k[1] in wiki_vocab_dict.token2id.keys():
        #check if it is not in the new db as well
        try:
            new_db.db((k[0],k[1]))
        except:#only add if it is not in the db in the reverse order
            term_pairs.add((k[0],k[1]))
            count +=1
    #compute Gensim and insert into db
    if count>=max_ins:
        count = 0
        #compute coherence
        term_pairs_ls = [[i[0],i[1]] for i in list(term_pairs)]
        cscore = CoherenceModel(topics=term_pairs,dictionary=wiki_vocab_dict,texts=pre_processed_wiki,coherence='c_npmi',processes=3,topn=2).get_coherence_per_topic()
        #inseert into db
        for i in tqdm(range(len(term_pairs_ls))):
            #if the key does not exist, insert it
            try:
                skeys = sorted(term_pairs_ls[i])
                new_db.db[(skeys[0],skeys[1])]
            except:
                new_db.db[(skeys[0],skeys[1])] = cscore[i]
        print('inserted {0} NPMI into database'.format(max_ins))
        term_pairs = set()
        
        
if count>0:
    term_pairs_ls = [[i[0],i[1]] for i in list(term_pairs)]
    cscore = CoherenceModel(topics=term_pairs,dictionary=wiki_vocab_dict,texts=pre_processed_wiki,coherence='c_npmi',processes=3,topn=2).get_coherence_per_topic()
    #inseert into db
    for i in tqdm(range(len(term_pairs_ls))):
        #if the key does not exist, insert it
        try:
            skeys = sorted(term_pairs_ls[i])
            new_db.db[(skeys[0],skeys[1])]
        except:
            new_db.db[(skeys[0],skeys[1])] = cscore[i]
    print('inserted {0} remaining NPMI into database'.format(count))

100%|███████████████████████████████████████████████████████████| 60000/60000 [00:08<00:00, 6806.40it/s]


inserted 60000 NPMI into database


100%|███████████████████████████████████████████████████████████| 60000/60000 [00:07<00:00, 7736.84it/s]


inserted 60000 NPMI into database


100%|███████████████████████████████████████████████████████████| 60000/60000 [00:14<00:00, 4012.96it/s]


inserted 60000 NPMI into database


100%|███████████████████████████████████████████████████████████| 37820/37820 [00:15<00:00, 2400.68it/s]

inserted 37820 remaining NPMI into database


In [34]:
with open('test.tmp','w') as txtfile:
    for t in term_pairs_ls:
        txtfile.write(t[0]+t[1]+'\n')